# in this work I intend to compare 2 big citys : Rio de janeiro and Lisbon. I will try to make clusters between trending venues from both cities


In [1]:
# first Let's search for coordinates for each city

In [2]:
#Now we will connect to Foursquare API

CLIENT_ID = 'secret' # your Foursquare ID
CLIENT_SECRET = 'secret' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)


Your credentails:
CLIENT_ID: JNPZF4KENJVWLOTSWMDSLX1DK3LGT502M3S30K1JBSHIWKTY
CLIENT_SECRET:0R4QIE0JXQ4KS1EQQDDMKS1WP3BQIINMRNWUCU0LBZ1T1FN1


In [462]:
import geocoder
from geopy.geocoders import Nominatim
adress_L='Lisboa,Portugal'
adress_RJ='Rio de Janeiro,Brasil'



geolocator = Nominatim(user_agent="mt_explorer")
location = geolocator.geocode(adress_L)
latitude_L = location.latitude
longitude_L = location.longitude

location = geolocator.geocode(adress_RJ)
latitude_RJ = location.latitude
longitude_RJ = location.longitude





print('Coordinates from Lisbon: latitude {}, longitude {},'.format(latitude_L,longitude_L))
print('Coordinates from Rio de Janeiro: latitude {}, longitude {},'.format(latitude_RJ,longitude_RJ))

Coordinates from Lisbon: latitude 38.7077507, longitude -9.1365919,
Coordinates from Rio de Janeiro: latitude -22.9110137, longitude -43.2093727,


In [463]:
import folium
map_Lisboa = folium.Map(location=[latitude_L, longitude_L], zoom_start=13)
folium.Marker(location=[latitude_L, longitude_L],popup="Lisboa")
  
    
map_Lisboa

In [16]:
map_RJ = folium.Map(location=[latitude_RJ, longitude_RJ], zoom_start=13)
folium.Marker(location=[latitude_RJ, longitude_RJ],popup="Rio de Janeiro")
  
    
map_RJ

In [18]:
LIMIT = 1000 # limit of number of venues returned by Foursquare API
radius = 1000 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude_L, 
    longitude_L,
    radius, 
    LIMIT)

# display URL
url

'https://api.foursquare.com/v2/venues/explore?&client_id=JNPZF4KENJVWLOTSWMDSLX1DK3LGT502M3S30K1JBSHIWKTY&client_secret=0R4QIE0JXQ4KS1EQQDDMKS1WP3BQIINMRNWUCU0LBZ1T1FN1&v=20180605&ll=38.7077507,-9.1365919&radius=1000&limit=1000'

In [20]:
import requests
results_L = requests.get(url).json()


In [21]:
LIMIT = 1000 # limit of number of venues returned by Foursquare API
radius = 1000 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude_RJ, 
    longitude_RJ,
    radius, 
    LIMIT)

# display URL
url

'https://api.foursquare.com/v2/venues/explore?&client_id=JNPZF4KENJVWLOTSWMDSLX1DK3LGT502M3S30K1JBSHIWKTY&client_secret=0R4QIE0JXQ4KS1EQQDDMKS1WP3BQIINMRNWUCU0LBZ1T1FN1&v=20180605&ll=-22.9110137,-43.2093727&radius=1000&limit=1000'

In [22]:
results_RJ = requests.get(url).json()


In [99]:
#results_RJ['response']['groups'][0]['items'][0]['venue']['categories'][0]['name']

In [122]:
nearby_venues_L

name             categories        lat  \
0   Praça do Comércio (Terreiro do Paço)                  Plaza  38.707960   
1                     Yes! Lisbon Hostel                 Hostel  38.709131   
2                       Cais das Colunas                  Plaza  38.706628   
3    Pousada de Lisboa, Terreiro do Paço                  Hotel  38.708294   
4                            Da Prata 52  Portuguese Restaurant  38.709613   
..                                   ...                    ...        ...   
95                       Lost Inn Lisbon        Bed & Breakfast  38.708252   
96                         Topo | Chiado                 Lounge  38.712481   
97                          Memmo Alfama                  Hotel  38.710304   
98             Vicente by Carnelentejana  Portuguese Restaurant  38.707779   
99                     Terraços do Carmo         Scenic Lookout  38.712332   

         lng  
0  -9.136657  
1  -9.137634  
2  -9.136121  
3  -9.137870  
4  -9.136404  
..       ...  
95 -9.144049  
96 -9.139901  
97 -9.130199  
98 -9.143833  
99 -9.139709  

[100 rows x 4 columns]

In [433]:
from pandas.io.json import json_normalize 
venues_RJ = results_RJ['response']['groups'][0]['items']    
nearby_venues_RJ = json_normalize(venues_RJ) # flatten JSON
venues_L = results_L['response']['groups'][0]['items']    
nearby_venues_L = json_normalize(venues_L) # flatten JSON

    

    

In [434]:

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng','venue.id']
nearby_venues_RJ =nearby_venues_RJ.loc[:, filtered_columns]

# filter the category for each row
nearby_venues_RJ['venue.categories'] = nearby_venues_RJ.apply(get_category_type, axis=1)

# clean columns
nearby_venues_RJ.columns = [col.split(".")[-1] for col in nearby_venues_RJ.columns]

nearby_venues_RJ.head()


name  categories        lat        lng                        id
0      Bar Kalango         Bar -22.912206 -43.211354  59061555780eee19afd32e64
1      La Fattoria        Café -22.912761 -43.208676  529f7b8911d2bdf8473414d4
2  Boteko do Peixe    Dive Bar -22.915066 -43.212634  56a4efa5498efaecc57de280
3    Bar da Frente         Bar -22.913597 -43.215222  4ca3ae977f84224b5fe7c658
4  Restaurante Una  Restaurant -22.913097 -43.214592  5b6b0ea1286fda002c00bae5

In [435]:
# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng','venue.id']
nearby_venues_L =nearby_venues_L.loc[:, filtered_columns]

# filter the category for each row
nearby_venues_L['venue.categories'] = nearby_venues_L.apply(get_category_type, axis=1)

# clean columns
nearby_venues_L.columns = [col.split(".")[-1] for col in nearby_venues_L.columns]



nearby_venues_L.head()

name             categories        lat  \
0  Praça do Comércio (Terreiro do Paço)                  Plaza  38.707960   
1                    Yes! Lisbon Hostel                 Hostel  38.709131   
2                      Cais das Colunas                  Plaza  38.706628   
3   Pousada de Lisboa, Terreiro do Paço                  Hotel  38.708294   
4                           Da Prata 52  Portuguese Restaurant  38.709613   

        lng                        id  
0 -9.136657  4b0588a2f964a52008d122e3  
1 -9.137634  4bb6f76f2ea195217473ac2f  
2 -9.136121  4cd2e48483e0721e88a55997  
3 -9.137870  54ece198498e4126b9c5699c  
4 -9.136404  54216a7e498e556bb4940785

In [436]:
nearby_venues_L.shape
nearby_venues_L['location']='Lisbon'
nearby_venues_RJ['location']='Rio de Janeiro'


In [442]:
import pandas as pd
df = pd.DataFrame( columns=list(nearby_venues_L))
df=df.append(nearby_venues_L)
df=df.append(nearby_venues_RJ)
df.reset_index(inplace=True)
df

index                                  name               categories  \
0        0  Praça do Comércio (Terreiro do Paço)                    Plaza   
1        1                    Yes! Lisbon Hostel                   Hostel   
2        2                      Cais das Colunas                    Plaza   
3        3   Pousada de Lisboa, Terreiro do Paço                    Hotel   
4        4                           Da Prata 52    Portuguese Restaurant   
..     ...                                   ...                      ...   
195     95                        Sabor Arretado  Comfort Food Restaurant   
196     96                   Joaquim e Terezinha     Brazilian Restaurant   
197     97                         Mag's Lanches                     Food   
198     98                             MegaMatte              Snack Place   
199     99                         Gallant Hotel                    Hotel   

           lat        lng                        id        location  
0    38.707960  -9.136657  4b0588a2f964a52008d122e3          Lisbon  
1    38.709131  -9.137634  4bb6f76f2ea195217473ac2f          Lisbon  
2    38.706628  -9.136121  4cd2e48483e0721e88a55997          Lisbon  
3    38.708294  -9.137870  54ece198498e4126b9c5699c          Lisbon  
4    38.709613  -9.136404  54216a7e498e556bb4940785          Lisbon  
..         ...        ...                       ...             ...  
195 -22.917728 -43.211805  55cb6335498e06fc70936156  Rio de Janeiro  
196 -22.918773 -43.213933  4d2925156e27a1434ae32124  Rio de Janeiro  
197 -22.911819 -43.214731  4dbebf17cda109aa6cd0c9e3  Rio de Janeiro  
198 -22.911622 -43.202445  4c938bc082b56dcb72a1c6aa  Rio de Janeiro  
199 -22.912514 -43.210548  4d74fef59d2fa14304b4f9d6  Rio de Janeiro  

[200 rows x 7 columns]

In [213]:
df['id'][0]

'4b0588a2f964a52008d122e3'

In [304]:


CLIENT_ID= 'secret'
CLIENT_SECRET = 'secret'

count=None
message=None
rating=None
verified=None
count=[]
message=[]
rating=[]
verified=[]
ok=[]
for i in range(0,len(df)):
    venue_id=df['id'][i]
    url = 'https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&v={}'.format(venue_id, CLIENT_ID, CLIENT_SECRET, VERSION)
    results = requests.get(url).json()
    try:
        count.append(results['response']['venue']['likes']['count'])
    except:
        count.append('empty')
    
    try:
        message.append(results['response']['venue']['price']['message'])
    except:
        message.append('empty')
    
    try:
        rating.append(results['response']['venue']['rating'])
    except:
        rating.append('empty')
    
    try:
        verified.append(results['response']['venue']['verified'])
    except:
        verified.append('empty')
    
    try:
        ok.append(results['response']['venue']['ok'])
    except:
        ok.append('empty')
    
    


In [298]:
results

{'meta': {'code': 429,
  'errorType': 'quota_exceeded',
  'errorDetail': 'Quota exceeded',
  'requestId': '5de44d2b949393001c8d947a'},
 'response': {}}

In [443]:
df['rating']=rating
df['Average_cost']=message
df['status']=ok
df['nr_of_reviews']=count
df['ok']=ok

In [439]:





df





index                                  name               categories  \
0        0  Praça do Comércio (Terreiro do Paço)                    Plaza   
1        1                    Yes! Lisbon Hostel                   Hostel   
2        2                      Cais das Colunas                    Plaza   
3        3   Pousada de Lisboa, Terreiro do Paço                    Hotel   
4        4                           Da Prata 52    Portuguese Restaurant   
..     ...                                   ...                      ...   
195     95                        Sabor Arretado  Comfort Food Restaurant   
196     96                   Joaquim e Terezinha     Brazilian Restaurant   
197     97                         Mag's Lanches                     Food   
198     98                             MegaMatte              Snack Place   
199     99                         Gallant Hotel                    Hotel   

           lat        lng                        id        location  rating  \
0    38.707960  -9.136657  4b0588a2f964a52008d122e3          Lisbon     9.4   
1    38.709131  -9.137634  4bb6f76f2ea195217473ac2f          Lisbon     9.2   
2    38.706628  -9.136121  4cd2e48483e0721e88a55997          Lisbon     9.0   
3    38.708294  -9.137870  54ece198498e4126b9c5699c          Lisbon     8.8   
4    38.709613  -9.136404  54216a7e498e556bb4940785          Lisbon     8.8   
..         ...        ...                       ...             ...     ...   
195 -22.917728 -43.211805  55cb6335498e06fc70936156  Rio de Janeiro     6.1   
196 -22.918773 -43.213933  4d2925156e27a1434ae32124  Rio de Janeiro     6.3   
197 -22.911819 -43.214731  4dbebf17cda109aa6cd0c9e3  Rio de Janeiro     5.9   
198 -22.911622 -43.202445  4c938bc082b56dcb72a1c6aa  Rio de Janeiro     6.0   
199 -22.912514 -43.210548  4d74fef59d2fa14304b4f9d6  Rio de Janeiro     5.5   

    Average_cost  status  nr_of_reviews     ok  
0          empty   False           2518  False  
1          empty   False             94  False  
2          empty   False            123  False  
3          empty   False             33  False  
4       Moderate   False            170  False  
..           ...     ...            ...    ...  
195        empty   False              6  False  
196     Moderate   False             14  False  
197        empty   False             10  False  
198        Cheap   False             15  False  
199        empty   False             29  False  

[200 rows x 12 columns]

In [444]:
df=df[['name','categories','rating','Average_cost','status','nr_of_reviews','ok','lat','lng','location']]
df

name               categories  rating  \
0    Praça do Comércio (Terreiro do Paço)                    Plaza     9.4   
1                      Yes! Lisbon Hostel                   Hostel     9.2   
2                        Cais das Colunas                    Plaza     9.0   
3     Pousada de Lisboa, Terreiro do Paço                    Hotel     8.8   
4                             Da Prata 52    Portuguese Restaurant     8.8   
..                                    ...                      ...     ...   
195                        Sabor Arretado  Comfort Food Restaurant     6.1   
196                   Joaquim e Terezinha     Brazilian Restaurant     6.3   
197                         Mag's Lanches                     Food     5.9   
198                             MegaMatte              Snack Place     6.0   
199                         Gallant Hotel                    Hotel     5.5   

    Average_cost  status  nr_of_reviews     ok        lat        lng  \
0          empty   False           2518  False  38.707960  -9.136657   
1          empty   False             94  False  38.709131  -9.137634   
2          empty   False            123  False  38.706628  -9.136121   
3          empty   False             33  False  38.708294  -9.137870   
4       Moderate   False            170  False  38.709613  -9.136404   
..           ...     ...            ...    ...        ...        ...   
195        empty   False              6  False -22.917728 -43.211805   
196     Moderate   False             14  False -22.918773 -43.213933   
197        empty   False             10  False -22.911819 -43.214731   
198        Cheap   False             15  False -22.911622 -43.202445   
199        empty   False             29  False -22.912514 -43.210548   

           location  
0            Lisbon  
1            Lisbon  
2            Lisbon  
3            Lisbon  
4            Lisbon  
..              ...  
195  Rio de Janeiro  
196  Rio de Janeiro  
197  Rio de Janeiro  
198  Rio de Janeiro  
199  Rio de Janeiro  

[200 rows x 10 columns]

In [447]:
#here we have the trending venues in Lisbon

for i in range(0,len(df)):
    label = '{}, {}'.format(df['name'][i], df['categories'][0])
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [df['lat'][i],df['lng'][i]],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#2186cc',
        fill_opacity=0.2,
        parse_html=False).add_to(map_Lisboa)
map_Lisboa

In [275]:
#here we have the trending venues in Rio de Janeiro

for i in range(0,len(df)):
    label = '{}, {}'.format(df['name'][i], df['categories'][0])
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [df['lat'][i],df['lng'][i]],
        radius=5,
        popup=label,
        color='green',
        fill=True,
        fill_color='#2186cc',
        fill_opacity=0.2,
        parse_html=False).add_to(map_RJ)
map_RJ

In [295]:
df

index                                  name               categories  \
0        0  Praça do Comércio (Terreiro do Paço)                    Plaza   
1        1                    Yes! Lisbon Hostel                   Hostel   
2        2                      Cais das Colunas                    Plaza   
3        3   Pousada de Lisboa, Terreiro do Paço                    Hotel   
4        4                           Da Prata 52    Portuguese Restaurant   
..     ...                                   ...                      ...   
195     95                        Sabor Arretado  Comfort Food Restaurant   
196     96                   Joaquim e Terezinha     Brazilian Restaurant   
197     97                         Mag's Lanches                     Food   
198     98                             MegaMatte              Snack Place   
199     99                         Gallant Hotel                    Hotel   

           lat        lng                        id Average_cost status  \
0    38.707960  -9.136657  4b0588a2f964a52008d122e3        empty  False   
1    38.709131  -9.137634  4bb6f76f2ea195217473ac2f        empty  empty   
2    38.706628  -9.136121  4cd2e48483e0721e88a55997        empty  empty   
3    38.708294  -9.137870  54ece198498e4126b9c5699c        empty  empty   
4    38.709613  -9.136404  54216a7e498e556bb4940785        empty  empty   
..         ...        ...                       ...          ...    ...   
195 -22.917728 -43.211805  55cb6335498e06fc70936156        empty  empty   
196 -22.918773 -43.213933  4d2925156e27a1434ae32124        empty  empty   
197 -22.911819 -43.214731  4dbebf17cda109aa6cd0c9e3        empty  empty   
198 -22.911622 -43.202445  4c938bc082b56dcb72a1c6aa        empty  empty   
199 -22.912514 -43.210548  4d74fef59d2fa14304b4f9d6        empty  empty   

    nr_of_reviews     ok  
0            2518  False  
1           empty  empty  
2           empty  empty  
3           empty  empty  
4           empty  empty  
..            ...    ...  
195         empty  empty  
196         empty  empty  
197         empty  empty  
198         empty  empty  
199         empty  empty  

[200 rows x 10 columns]

In [448]:
from sklearn import preprocessing
scaler = preprocessing.StandardScaler()
# we need to normalize our continuous variables.
normalized_rating = scaler.fit_transform(df[['rating']])
normalized_nr_of_reviews = scaler.fit_transform(df[['nr_of_reviews']])


In [449]:
from sklearn.preprocessing import LabelEncoder 
  
#now we go transform our qualitative variables into one hot encoding    
    
le = LabelEncoder() 
 
train={}    
train=pd.DataFrame(train)
train['categories']= le.fit_transform(df['categories']) 
train['Average_cost']= le.fit_transform(df['Average_cost']) 
train['status']= le.fit_transform(df['status']) 
train['ok']= le.fit_transform(df['ok']) 
train['rating']=normalized_rating
train['nr_of_reviews']=normalized_nr_of_reviews
train

categories  Average_cost  status  ok    rating  nr_of_reviews
0            59             4       0   0  1.475437       8.445773
1            41             4       0   0  1.280015      -0.125941
2            59             4       0   0  1.084593      -0.023392
3            42             4       0   0  0.889171      -0.341649
4            60             2       0   0  0.889171       0.142809
..          ...           ...     ...  ..       ...            ...
195          22             4       0   0 -1.749028      -0.437126
196          12             2       0   0 -1.553606      -0.408836
197          29             4       0   0 -1.944450      -0.422981
198          72             0       0   0 -1.846739      -0.405300
199          42             4       0   0 -2.335294      -0.355793

[200 rows x 6 columns]

In [450]:
from sklearn.cluster import KMeans

kclusters=5
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(train)


In [451]:
output={'k-cluster':kmeans.labels_}
output_final=pd.DataFrame(output)
df['output']=output_final
df

C:\Users\alexa\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


name               categories  rating  \
0    Praça do Comércio (Terreiro do Paço)                    Plaza     9.4   
1                      Yes! Lisbon Hostel                   Hostel     9.2   
2                        Cais das Colunas                    Plaza     9.0   
3     Pousada de Lisboa, Terreiro do Paço                    Hotel     8.8   
4                             Da Prata 52    Portuguese Restaurant     8.8   
..                                    ...                      ...     ...   
195                        Sabor Arretado  Comfort Food Restaurant     6.1   
196                   Joaquim e Terezinha     Brazilian Restaurant     6.3   
197                         Mag's Lanches                     Food     5.9   
198                             MegaMatte              Snack Place     6.0   
199                         Gallant Hotel                    Hotel     5.5   

    Average_cost  status  nr_of_reviews     ok        lat        lng  \
0          empty   False           2518  False  38.707960  -9.136657   
1          empty   False             94  False  38.709131  -9.137634   
2          empty   False            123  False  38.706628  -9.136121   
3          empty   False             33  False  38.708294  -9.137870   
4       Moderate   False            170  False  38.709613  -9.136404   
..           ...     ...            ...    ...        ...        ...   
195        empty   False              6  False -22.917728 -43.211805   
196     Moderate   False             14  False -22.918773 -43.213933   
197        empty   False             10  False -22.911819 -43.214731   
198        Cheap   False             15  False -22.911622 -43.202445   
199        empty   False             29  False -22.912514 -43.210548   

           location  output  
0            Lisbon       1  
1            Lisbon       3  
2            Lisbon       1  
3            Lisbon       3  
4            Lisbon       1  
..              ...     ...  
195  Rio de Janeiro       0  
196  Rio de Janeiro       2  
197  Rio de Janeiro       0  
198  Rio de Janeiro       4  
199  Rio de Janeiro       3  

[200 rows x 11 columns]

In [465]:
#here we have the trending venues in Lisbon in each cluster.

# create map
# set color scheme for the clusters
import numpy as np
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(df['lat'], df['lng'], df['name'], df['output']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_Lisboa)
map_Lisboa

In [464]:
#here we have the trending venues in Rio de Janeiro in each cluster.
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(df['lat'], df['lng'], df['name'], df['output']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_RJ)
map_RJ

In [455]:
#characteristics from cluster 1
df.loc[df['output'] == 0][['name','categories','rating','Average_cost','nr_of_reviews','location']]

name               categories  rating  \
19           Igreja de Santo António da Sé                   Church     8.8   
31   Igreja de Santa Maria Maior de Lisboa                   Church     8.6   
37                              The George                Gastropub     8.4   
87                          Palácio Chiado               Food Court     8.9   
90          Sama Sama- Crêpe And Juice Bar                 Creperie     8.5   
102                        Boteko do Peixe                 Dive Bar     8.5   
109                         Noo Cachaçaria             Cocktail Bar     8.2   
123                          Aussie Coffee              Coffee Shop     7.6   
125               Estádio Figueira de Melo         Football Stadium     7.7   
128                             Bar Madrid                 Dive Bar     8.2   
133         Dom Barcelos Galeteria & Grill      Fried Chicken Joint     7.5   
136                             Kopenhagen           Chocolate Shop     7.3   
154                            Polo Têxtil              Fabric Shop     7.2   
155                   Bar e Lanchonete Rex      Fried Chicken Joint     6.6   
156                                   Soho              Coffee Shop     7.0   
160                  AM/PM - Posto Lobinho        Convenience Store     6.8   
172                       Boteco do Divino                     Food     6.5   
181                              Mineirart   Furniture / Home Store     6.4   
182                     Americanas Express         Department Store     6.0   
183                 Feira Livre de Domingo           Farmers Market     6.5   
189                 Tortamania Cidade Nova              Coffee Shop     6.1   
195                         Sabor Arretado  Comfort Food Restaurant     6.1   
197                          Mag's Lanches                     Food     5.9   

    Average_cost  nr_of_reviews        location  
19         empty            402          Lisbon  
31         empty            187          Lisbon  
37     Expensive             96          Lisbon  
87         empty            264          Lisbon  
90      Moderate             11          Lisbon  
102        Cheap             12  Rio de Janeiro  
109    Expensive             63  Rio de Janeiro  
123        Cheap              8  Rio de Janeiro  
125        empty             11  Rio de Janeiro  
128        Cheap             78  Rio de Janeiro  
133     Moderate             97  Rio de Janeiro  
136        empty             53  Rio de Janeiro  
154        empty             66  Rio de Janeiro  
155        Cheap              7  Rio de Janeiro  
156        Cheap             26  Rio de Janeiro  
160        empty            106  Rio de Janeiro  
172        empty              6  Rio de Janeiro  
181        empty              7  Rio de Janeiro  
182        empty              0  Rio de Janeiro  
183        empty             37  Rio de Janeiro  
189        Cheap              4  Rio de Janeiro  
195        empty              6  Rio de Janeiro  
197        empty             10  Rio de Janeiro

In [456]:
#characteristics from cluster 2
df.loc[df['output'] == 1][['name','categories','rating','Average_cost','nr_of_reviews','location']]

name             categories  rating  \
0    Praça do Comércio (Terreiro do Paço)                  Plaza     9.4   
2                        Cais das Colunas                  Plaza     9.0   
4                             Da Prata 52  Portuguese Restaurant     8.8   
5                                 Basilio             Restaurant     9.4   
11                           Maria Catita  Portuguese Restaurant     8.6   
12                     Praça do Município                  Plaza     8.5   
22                          Organi Chiado             Restaurant     9.0   
24                                  Qosqo    Peruvian Restaurant     8.3   
27                               O Chiado  Portuguese Restaurant     8.9   
29           Largo de Santo António da Sé                  Plaza     8.4   
34                      Cruzes Credo Café  Portuguese Restaurant     8.7   
35                                  Prado  Portuguese Restaurant     8.4   
40                     D. Afonso, o Gordo  Portuguese Restaurant     8.2   
43                    Cantinho do Avillez  Portuguese Restaurant     9.0   
45                               Belcanto             Restaurant     9.3   
49                                   Alma  Portuguese Restaurant     8.9   
53                               Alpendre     Seafood Restaurant     8.7   
54                            Navegadoors             Restaurant     8.6   
57                     Leitaria Camponeza  Portuguese Restaurant     8.6   
58                                 O Arco  Portuguese Restaurant     8.7   
62                   Sacramento do Chiado  Portuguese Restaurant     8.9   
65                        Largo do Chiado                  Plaza     9.4   
71                Floresta das Escadinhas  Portuguese Restaurant     8.8   
72                            Café Lisboa             Restaurant     8.6   
73              Le Petit Café Restaurante  Portuguese Restaurant     8.8   
74      Miradouro do Castelo de São Jorge         Scenic Lookout     9.5   
76                         Nata De Lisboa            Pastry Shop     8.4   
77                         Largo do Carmo                  Plaza     9.0   
78                         Chapito à Mesa  Portuguese Restaurant     8.3   
85                            Pensão Amor              Nightclub     9.0   
89                        Pizzaria Lisboa            Pizza Place     8.3   
98              Vicente by Carnelentejana  Portuguese Restaurant     8.8   
99                      Terraços do Carmo         Scenic Lookout     8.5   
104                       Restaurante Una             Restaurant     8.3   
108                             Botto Bar                    Pub     7.9   
111                      Petshop Apoteose              Pet Store     7.8   
113             G.R.E.S. Unidos da Tijuca           Samba School     8.1   
118                Rua Santo Cristo,  232    Rental Car Location     8.3   
119                           O Forno Rio            Pizza Place     8.3   
124                G.R.E.S. Estácio de Sá           Samba School     7.8   
126                           Villa Grill             Restaurant     7.1   
130                            Heavy Duty              Rock Club     7.5   
131                           Pizza & Etc            Pizza Place     8.1   
142                        Filet & Folhas            Salad Place     7.2   
143                 Circo Crescer e Viver  Performing Arts Venue     7.5   
146                                Subway         Sandwich Place     7.2   
151                   Ulysses Restaurante             Restaurant     6.7   
164                   Feedback Steakhouse             Restaurant     6.7   
168                 G.R.E.S. São Clemente           Samba School     6.3   
173                                Subway         Sandwich Place     6.5   
175                       Pimenta Carioca             Restaurant     6.4   
184                          Manada Grill             Restaurant     6.3   
185      

In [457]:
#characteristics from cluster 3
df.loc[df['output'] == 2][['name','categories','rating','Average_cost','nr_of_reviews','location']]

name            categories  rating Average_cost  \
13                    Outro Lado                   Bar     8.7     Moderate   
23               Taberna Moderna                   Bar     8.4    Expensive   
25            Queijaria Nacional           Cheese Shop     8.3        empty   
33                Fábrica Lisboa                Bakery     8.5        Cheap   
41                    Mesa Kreol    African Restaurant     8.2     Moderate   
..                           ...                   ...     ...          ...   
180                     Polo Mix  Brazilian Restaurant     6.5     Moderate   
186  Restaurante Caminho da Roça  Brazilian Restaurant     6.4     Moderate   
187              Canteiro Bistrô                Bistro     6.1        empty   
194   Padaria e Confeitaria Milú                Bakery     6.1        Cheap   
196          Joaquim e Terezinha  Brazilian Restaurant     6.3     Moderate   

     nr_of_reviews        location  
13              12          Lisbon  
23             162          Lisbon  
25              21          Lisbon  
33             277          Lisbon  
41              14          Lisbon  
..             ...             ...  
180             23  Rio de Janeiro  
186              3  Rio de Janeiro  
187             23  Rio de Janeiro  
194             21  Rio de Janeiro  
196             14  Rio de Janeiro  

[62 rows x 6 columns]

In [458]:
#characteristics from cluster 4
df.loc[df['output'] == 3][['name','categories','rating','Average_cost','nr_of_reviews','location']]

name                 categories  rating  \
1                     Yes! Lisbon Hostel                     Hostel     9.2   
3    Pousada de Lisboa, Terreiro do Paço                      Hotel     8.8   
7                             India Gate          Indian Restaurant     8.9   
8                     Home Lisbon Hostel                     Hostel     9.3   
9            Lisbon Shop - Pátio da Galé                  Gift Shop     8.4   
10                             Fragoleto             Ice Cream Shop     8.4   
15                 Conserveira de Lisboa               Gourmet Shop     8.3   
16                    Napoleão Wine Shop               Liquor Store     8.4   
18                      Brown's Downtown                      Hotel     8.7   
20                            Tasca Kome        Japanese Restaurant     8.3   
21                        Gelato Therapy             Ice Cream Shop     8.4   
26            Liquid - Sumos & Smoothies                  Juice Bar     8.4   
28                  Living Lounge Hostel                     Hostel     9.0   
30                    Loja das Conservas               Gourmet Shop     8.7   
38                               Santini             Ice Cream Shop     9.1   
39                Brown ´s Hotel Central                      Hotel     8.9   
46                               Amorino             Ice Cream Shop     8.9   
47                        Amorino Chiado             Ice Cream Shop     9.1   
55                                  Grom             Ice Cream Shop     8.7   
63                       Natraj Tandoori          Indian Restaurant     8.7   
64                   Hostel Inn possible                     Hostel     8.7   
70    Lisbon Short Stay Apartments Baixa                      Hotel     8.4   
75                     Hotel Santa Justa                      Hotel     8.9   
86           Museu Arqueológico do Carmo             History Museum     8.8   
94                              Caximbar                     Lounge     8.3   
96                         Topo | Chiado                     Lounge     8.7   
97                          Memmo Alfama                      Hotel     8.8   
107                   Mahmud Restaurante  Middle Eastern Restaurant     7.6   
110                         Bar do Elias  Middle Eastern Restaurant     8.3   
117                   Emporio Città Nova         Italian Restaurant     8.1   
121                       Sorvete Itália             Ice Cream Shop     7.2   
129                        Baile do Bené                Music Venue     7.2   
140                     Academia Rio2016                        Gym     6.7   
141                   Academia Body Line             Gymnastics Gym     7.3   
147                   Academia Body Line       Gym / Fitness Center     7.5   
152              Academia Ramper Fitness       Gym / Fitness Center     6.9   
166                       Estúdio sonora                Music Venue     6.8   
178            Museu do Primeiro Reinado             History Museum     6.6   
188                  Morro de São Carlos                   Mountain     6.0   
192           Spoleto Culinária Italiana         Italian Restaurant     5.9   
199                        Gallant Hotel                      Hotel     5.5   

    Average_cost  nr_of_reviews        location  
1          empty             94          Lisbon  
3          empty             33          Lisbon  
7       Moderate             14          Lisbon  
8          empty             60          Lisbon  
9          empty             20          Lisbon  
10         Cheap             48          Lisbon  
15         empty             73          Lisbon  
16         empty             35          Lisbon  
18         empty             57          Lisbon  
20      Moderate             79          Lisbon  
21         Cheap             70          Lisbon  
26         Cheap             52          Lisbon  
28         empty             33          Lisbon  
30         empty 

In [459]:
#characteristics from cluster 5
df.loc[df['output'] == 4][['name','categories','rating','Average_cost','nr_of_reviews','location']]

name  \
6                                Nova Pombalina   
14                                         Nova   
17                      Tágide Wine & Tapas Bar   
32                   Ao 26 – vegan food project   
36                             Ribeira das Naus   
52                    São Luiz Teatro Municipal   
67                                    Wine Not?   
79                          Garrafeira Nacional   
81          By the Wine - José Maria da Fonseca   
82                           Armazéns do Chiado   
83                              Lisbon Art Stay   
92                                  Sol e Pesca   
138             São Cristóvão Futebol e Regatas   
144                           All In Sports Bar   
148                            Poró Restaurante   
150  Casa Vila da Feira e Terras de Santa Maria   
162                       Boulevard Cidade Nova   
190               SuperVia - Estação Leopoldina   
191                                 Vila Mimosa   
193                       Mundial Supermercados   
198                                   MegaMatte   

                        categories  rating Average_cost  nr_of_reviews  \
6                      Snack Place     8.8        Cheap             89   
14                        Wine Bar     8.5     Moderate             14   
17                Tapas Restaurant     8.6    Expensive            136   
32   Vegetarian / Vegan Restaurant     8.9     Moderate            116   
36                      Waterfront     8.9        empty            209   
52                         Theater     9.3        empty            113   
67                Tapas Restaurant     8.2    Expensive             26   
79                       Wine Shop     8.7        empty             74   
81                        Wine Bar     9.5     Moderate            536   
82                   Shopping Mall     8.2        empty           1010   
83                        Wine Bar     8.2     Moderate              8   
92                Tapas Restaurant     9.0        Cheap            258   
138                   Soccer Field     7.4        empty             16   
144                     Sports Bar     6.9        Cheap             12   
148  Vegetarian / Vegan Restaurant     7.0     Moderate             12   
150                    Sports Club     7.4        empty             39   
162                 Shopping Plaza     6.7        empty             57   
190                  Train Station     5.8        empty             40   
191                     Strip Club     6.0    Expensive             48   
193                    Supermarket     5.8        empty             82   
198                    Snack Place     6.0        Cheap             15   

           location  
6            Lisbon  
14           Lisbon  
17           Lisbon  
32           Lisbon  
36           Lisbon  
52           Lisbon  
67           Lisbon  
79           Lisbon  
81           Lisbon  
82           Lisbon  
83           Lisbon  
92           Lisbon  
138  Rio de Janeiro  
144  Rio de Janeiro  
148  Rio de Janeiro  
150  Rio de Janeiro  
162  Rio de Janeiro  
190  Rio de Janeiro  
191  Rio de Janeiro  
193  Rio de Janeiro  
198  Rio de Janeiro